This code reads in a dataframe and (1) explores the topics and helps to determine the best number of topics to use, and (2) develops the model and data for charting topics through time of the "Data for Research" JSTOR data.  It is adapted from that of Charissa Rentier (https://github.com/charissarentier/mental-health-discourse).  In the process, it creates many data files (in pickle format) for reference.  For bulk production of pyLDAvis files (once the number of topics is determined) see the notebook "Topic Files Bulk Processing."

The base dataframe, created through the "Dataframe-with-Text", contains the following columns: index, id, type, title, auth1, year, lang, citations, text, text_noent, tokenized_text, tokenized_nopunc_lower, tokenized_nopunc_lower_nostop, tokenized_nopunc_lower_nostop_extra, tokenized_nopunc_lower_nostop_extra_lemmatized.  Most of the columns, from text_noent to tokenized_nopunc_lower_nostop_extra, can be dropped.  The last column, tokenized_nopunc_lower_nostop_extra_lemmatized, is a single list of words for each article.

The assumption is that all of the input files, this notebook, and the output files, all are in the same directory.  This can obviously be changed, but it keeps things a bit easier.  To develop the model for the entire corpus, it is important to run separately the "research_article" and "book-review" types.  The strategy is first to filter the dataframe accordingly and then run the processes.

In [1]:
import os
import sys
import json
import datetime
import pickle
import gc
import time

from operator import itemgetter
from collections import defaultdict

import pandas as pd
import numpy as np

import gensim
from gensim import corpora, models
from sklearn.feature_extraction.text import CountVectorizer
from gensim import corpora, models, similarities, matutils
from gensim.models.ldamodel import LdaModel
from gensim.models.ldamulticore import LdaMulticore

import pprint
pp = pprint.PrettyPrinter(indent=4)

import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

In [2]:
with open('clean_data_full.pickle', 'rb') as file:
    art = pickle.load(file)

# with open('book_review_small.pickle', 'rb') as file:
#     art = pickle.load(file)

In [3]:

art.head()

index                                                 id              type  \
0      1  [C:\Users\msatlow\Dropbox\AJSProject\data\jsto...  research-article   
1      2  [C:\Users\msatlow\Dropbox\AJSProject\data\jsto...  research-article   
2      3  [C:\Users\msatlow\Dropbox\AJSProject\data\jsto...  research-article   
3      4  [C:\Users\msatlow\Dropbox\AJSProject\data\jsto...  research-article   
4      5  [C:\Users\msatlow\Dropbox\AJSProject\data\jsto...  research-article   

                                               title                auth1  \
0  The Beginnings of Modern Hebrew Literature: Pe...       Arnold J. Band   
1        Sholem Aleichem: Mythologist of the Mundane     David G. Roskies   
2  "A Word for My Blood:" A Reading of Kadya Molo...  Kathryn Hellerstein   
3  Warding off Chaos: Repetition and Obsession in...          Janet Hadda   
4    Binary Oppositions in the Poetry of Amir Gilboa        Warren Bargad   

   year lang                                          citations  \
0  1988  eng  [(Bate, The Burden of the Past and the English...   
1  1988  eng  [(Roskies, Prooftexts, 1986, \nDavid G. Roskie...   
2  1988  eng  [(Molodowsky, Fun mayn elterzeydns yerushe, , ...   
3  1988  eng  [(Thorner, International Journal of Psycho-Ana...   
4  1988  eng  [(Tamir-Ghez, PTL, 1978, \nNomi Tamir-Ghez, "B...   

                                                text  \
0                                                      
1   page sequence 1 SHOLEM ALEICHEM MYTHOLOGIST O...   
2   page sequence 1 A WORD FOR MY BLOOD A READING...   
3   page sequence 1 WARDING OFF CHAOS REPETITION ...   
4   page sequence 1 BINARY OPPOSITIONS IN THE POE...   

                                          text_noent  \
0                                                      
1   page sequence 1 SHOLEM ALEICHEM MYTHOLOGIST O...   
2   page sequence 1 A WORD FOMY BLOOD A READING O...   
3   page sequence 1 WARDING OFF CHAOS REPETITION ...   
4   page sequence 1 BINARY OPPOSITIONS IN POETRY ...   

                                      tokenized_text  \
0                                                 []   
1  [page, sequence, 1, SHOLEM, ALEICHEM, MYTHOLOG...   
2  [page, sequence, 1, A, WORD, FOMY, BLOOD, A, R...   
3  [page, sequence, 1, WARDING, OFF, CHAOS, REPET...   
4  [page, sequence, 1, BINARY, OPPOSITIONS, IN, P...   

                                    tokenized_nopunc  \
0                                                 []   
1  [page, sequence, SHOLEM, ALEICHEM, MYTHOLOGIST...   
2  [page, sequence, A, WORD, FOMY, BLOOD, A, READ...   
3  [page, sequence, WARDING, OFF, CHAOS, REPETITI...   
4  [page, sequence, BINARY, OPPOSITIONS, IN, POET...   

                              tokenized_nopunc_lower  \
0                                                 []   
1  [page, sequence, sholem, aleichem, mythologist...   
2  [page, sequence, a, word, fomy, blood, a, read...   
3  [page, sequence, warding, off, chaos, repetiti...   
4  [page, sequence, binary, oppositions, in, poet...   

                       tokenized_nopunc_lower_nostop  \
0                                                 []   
1  [sholem, aleichem, mythologist, mundane, roski...   
2  [word, fomy, blood, reading, kadya, molodowsky...   
3  [warding, chaos, repetition, obsession, poetry...   
4  [binary, oppositions, poetry, amigilboa, warre...   

                 tokenized_nopunc_lower_nostop_extra  \
0                                                 []   
1  [sholem, aleichem, mythologist, mundane, roski...   
2  [fomy, blood, reading, kadya, molodowsky, froy...   
3  [warding, chaos, repetition, obsession, poetry...   
4  [binary, oppositions, poetry, amigilboa, warre...   

      tokenized_nopunc_lower_nostop_extra_lemmatized  
0                                                 []  
1  [sholem, aleichem, mythologist, mundane, roski...  
2  [fomy, blood, reading, kadya, molodowsky, froy...  
3  [warding, chaos, repetition, obsession, poetry...  
4  [binary, oppo

In [4]:
# List of Extra Stop words
stopwords = [
    'week','another','thing','month','day','come',
    'york','away','left','wrote','came','tell','asked',
    'left','right','hand','point','often','talk','head','point','ago','whether',
    'hour','group','became','become','becomes','often','sometimes','usually','page','sequence','doi','p'
    ]

In [5]:
# Remove Extra Stop Words
art['article_text_nostop_extra'] = [[word for word in x if not word in stopwords and len(word)>3] for x in art['tokenized_nopunc_lower_nostop_extra_lemmatized']]

In [6]:
art['article_text_nostop_extra']

0                                                      []
1       [sholem, aleichem, mythologist, mundane, roski...
2       [fomy, blood, reading, kadya, molodowsky, froy...
3       [warding, chaos, repetition, obsession, poetry...
4       [binary, opposition, poetry, amigilboa, warren...
5       [kill, youordinary, common, sense, maybe, begi...
6       [ghost, writing, philip, roth, portrait, artis...
7       [reinventing, bruno, schulz, cynthia, ozics, m...
8       [mishnaic, literary, history, history, mishnai...
9       [ashi, amora, transition, ocontinuity, study, ...
10      [light, mozarabic, toledo, norman, roth, medie...
11      [love, poetry, yehuda, amichai, glenda, abrams...
12      [martin, goodman, roman, galilee, centre, post...
13      [jack, lightstone, commerce, sacred, mediation...
14      [judith, baskin, pharaoh, counsellor, jethro, ...
15      [stephen, passamaneck, traditional, sale, shul...
16      [wistrich, socialism, dilemma, assimilation, g...
17      [joshu

In [7]:
art['string'] = [' '.join(x) for x in art['article_text_nostop_extra']]

In [8]:
newart=art.copy()

In [9]:
newart=newart[(newart['year']>1995) & (newart['year']<2000)]
newart=newart[newart['type']=='research-article']
newart.head()


index                                                 id  \
236    288  [C:\Users\msatlow\Dropbox\AJSProject\data\jsto...   
237    289  [C:\Users\msatlow\Dropbox\AJSProject\data\jsto...   
238    290  [C:\Users\msatlow\Dropbox\AJSProject\data\jsto...   
261    317  [C:\Users\msatlow\Dropbox\AJSProject\data\jsto...   
262    318  [C:\Users\msatlow\Dropbox\AJSProject\data\jsto...   

                 type                                              title  \
236  research-article  From after Death to Afterlife: Martyrdom and I...   
237  research-article  "Do the Dead Know?" The Representation of Deat...   
238  research-article  Haim Gouri and "The Jewish People Who Have Bee...   
261  research-article   Isaac Abarbanel's "Stance toward Tradition": ...   
262  research-article  Biblical Hebrews and the Rhetoric of Republica...   

               auth1  year lang  \
236  Shmuel Shepkaru  1999  eng   
237      Aryeh Cohen  1999  eng   
238    Reuven Shoham  1999  eng   
261       Eric Lawee  1997  eng   
262    Miriam Bodian  1997  eng   

                                             citations  \
236  [(Raphael, Jewish Views of the Afterlife, 1994...   
237  [(, , , \nJacques Derrida, "Adieu," Critical I...   
238  [(, , , \nMerhavya, 1949), (, , , \nTel Aviv, ...   
261  [(Bate, The Burden of the Past and the English...   
262  [(Baron, The Crisis of the Early Italian Renai...   

                                                  text  \
236   page sequence 1 FROM AFTER DEATH TO AFTERLIFE...   
237   page sequence 1 DO THE DEAD KNOW THE REPRESEN...   
238   page sequence 1 HAIM GOURI AND THE JEWISH PEO...   
261   page sequence 1 ISAAC ABARBANEL S STANCE TOWA...   
262   page sequence 1 BIBLICAL HEBREWS AND THE RHET...   

                                            text_noent  \
236   page sequence 1 FROM AFTEDEATH TO AFTERLIFE M...   
237   page sequence 1 DO DEAD KNOW REPRESENTATION O...   
238   page sequence 1 HAIM GOURI AND JEWISH PEOPLE ...   
261   page sequence 1 ISAAC ABARBANEL S STANCE TOWA...   
262   page sequence 1 BIBLICAL HEBREWS AND RHETORIC...   

                                        tokenized_text  \
236  [page, sequence, 1, FROM, AFTEDEATH, TO, AFTER...   
237  [page, sequence, 1, DO, DEAD, KNOW, REPRESENTA...   
238  [page, sequence, 1, HAIM, GOURI, AND, JEWISH, ...   
261  [page, sequence, 1, ISAAC, ABARBANEL, S, STANC...   
262  [page, sequence, 1, BIBLICAL, HEBREWS, AND, RH...   

                                      tokenized_nopunc  \
236  [page, sequence, FROM, AFTEDEATH, TO, AFTERLIF...   
237  [page, sequence, DO, DEAD, KNOW, REPRESENTATIO...   
238  [page, sequence, HAIM, GOURI, AND, JEWISH, PEO...   
261  [page, sequence, ISAAC, ABARBANEL, S, STANCE, ...   
262  [page, sequence, BIBLICAL, HEBREWS, AND, RHETO...   

                                tokenized_nopunc_lower  \
236  [page, sequence, from, aftedeath, to, afterlif...   
237  [page, sequence, do, dead, know, representatio...   
238  [page, sequence, haim, gouri, and, jewish, peo...   
261  [page, sequence, isaac, abarbanel, s, stance, ...   
262  [page, sequence, biblical, hebrews, and, rheto...   

                         tokenized_nopunc_lower_nostop  \
236  [aftedeath, afterlife, martyrdom, recompense, ...   
237  [dead, know, representation, death, bavli, ary...   
238  [haim, gouri, people, seriously, injured, reuv...   
261  [isaac, abarbanel, stance, tradition, case, at...   
262  [biblical, hebrews, rhetoric, republicanism, s...   

                   tokenized_nopunc_lower_nostop_extra  \
236  [aftedeath, afterlife, martyrdom, recompense, ...   
237  [dead, representation, death, bavli, aryeh, co...   
238  [haim, gouri, people, seriously, injured, reuv...   
261  [isaac, abarbanel, stance, tradition, case, at...   
262  [biblical, hebrews, rhetoric, republicanism, s...   

        tokenized_nopunc_lower_nostop_extra_lemmatized  \
236  [aftedeath, afterlife, martyrdom, recompense, ...   
237  [dead, representation, death, bav

In [11]:
vec = CountVectorizer(max_df =.95,min_df = 10,stop_words='english')
counts = vec.fit_transform(newart['string']).transpose()

In [12]:
counts.shape

(867, 30)

In [13]:
# # import corpus
# with open('pickled_files/full_set_countvec_corpus.pickle','rb') as file:
#     corpus = pickle.load(file)

corpus = matutils.Sparse2Corpus(counts)

# # export corpus
# with open('pickled_files/full_set_countvec_corpus.pickle','wb') as file:
#     pickle.dump(corpus,file)

In [14]:
 # load previously saved dictionary

# with open('pickled_files/full_set_countvec_dict.pickle', 'rb') as file:
#     dictionary = pickle.load(file)

dictionary = dict((v, k) for k, v in vec.vocabulary_.items())

In [15]:
len(dictionary)

867

In [16]:
# Dictionary to store topics in
validation_50p = {}

In [17]:
# Function to calculate and store models for validating choice for no_of_topics
def cross_val_topics_50p(no_of_topics):
    model = LdaModel(corpus, num_topics=no_of_topics, id2word = dictionary, passes=50, alpha='auto', eval_every=2000)
    globals()['ldamodel_%dt_50p_autoalpha_newtest_val' % no_of_topics] = model
    model.save('lda_{}t_50p_autoalpha_newtest_val.model'.format(no_of_topics))
    validation_50p[no_of_topics] = model.print_topics(num_topics=-1, num_words=50)

In [18]:
# Loop through 12-30 topics to see optimal number of topics
for i in np.arange(12,31):
    print('Running LDA with 50 passes for {} topics...'.format(i))
    cross_val_topics_50p(i)
    with open('dict_topics_from_validation_research_50p.pickle', 'wb') as file:
        pickle.dump(validation_50p, file)

2020-07-26 17:41:19,488 : INFO : using autotuned alpha, starting with [0.083333336, 0.083333336, 0.083333336, 0.083333336, 0.083333336, 0.083333336, 0.083333336, 0.083333336, 0.083333336, 0.083333336, 0.083333336, 0.083333336]
2020-07-26 17:41:19,495 : INFO : using symmetric eta at 0.08333333333333333
2020-07-26 17:41:19,496 : INFO : using serial LDA version on this node
2020-07-26 17:41:19,638 : INFO : running online (multi-pass) LDA training, 12 topics, 50 passes over the supplied corpus of 30 documents, updating model once every 30 documents, evaluating perplexity every 30 documents, iterating 50x with a convergence threshold of 0.001000


Running LDA with 50 passes for 12 topics...


2020-07-26 17:41:19,855 : INFO : -7.572 per-word bound, 190.3 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 17:41:19,856 : INFO : PROGRESS: pass 0, at document #30/30
2020-07-26 17:41:19,897 : INFO : optimized alpha [0.13399486, 0.13405852, 0.13493378, 0.14428765, 0.13095671, 0.13996276, 0.13980177, 0.14348309, 0.13486175, 0.139436, 0.1373708, 0.14669743]
2020-07-26 17:41:19,903 : INFO : topic #4 (0.131): 0.013*"woman" + 0.008*"death" + 0.008*"wife" + 0.007*"world" + 0.007*"nation" + 0.006*"spirit" + 0.006*"torah" + 0.006*"according" + 0.006*"order" + 0.005*"rabbi"
2020-07-26 17:41:19,904 : INFO : topic #1 (0.134): 0.022*"maimonides" + 0.010*"community" + 0.010*"rabbi" + 0.009*"death" + 0.007*"tradition" + 0.006*"torah" + 0.006*"suffering" + 0.006*"story" + 0.005*"authority" + 0.005*"century"
2020-07-26 17:41:19,905 : INFO : topic #7 (0.143): 0.013*"torah" + 0.008*"rabbi" + 0.007*"tradition" + 0.007*"world" + 0.007*"maimonides" + 0.006*"soul

2020-07-26 17:41:20,831 : INFO : optimized alpha [0.041130207, 0.04662471, 0.038901906, 0.06543849, 0.04224888, 0.060613807, 0.060822755, 0.051095106, 0.043054707, 0.046675526, 0.04000693, 0.08187382]
2020-07-26 17:41:20,834 : INFO : topic #2 (0.039): 0.021*"rabbi" + 0.016*"voice" + 0.016*"synagogue" + 0.012*"collection" + 0.011*"writing" + 0.010*"prayer" + 0.010*"praise" + 0.009*"service" + 0.008*"read" + 0.008*"example"
2020-07-26 17:41:20,835 : INFO : topic #10 (0.040): 0.076*"nation" + 0.037*"torah" + 0.025*"world" + 0.016*"drama" + 0.012*"commandment" + 0.012*"witness" + 0.011*"roman" + 0.011*"midrash" + 0.009*"people" + 0.008*"judgment"
2020-07-26 17:41:20,837 : INFO : topic #6 (0.061): 0.055*"community" + 0.030*"rabbi" + 0.023*"political" + 0.017*"court" + 0.017*"century" + 0.016*"government" + 0.012*"authority" + 0.009*"father" + 0.008*"city" + 0.008*"people"
2020-07-26 17:41:20,838 : INFO : topic #3 (0.065): 0.044*"torah" + 0.013*"midrash" + 0.012*"scripture" + 0.012*"world" +

2020-07-26 17:41:21,808 : INFO : topic #10 (0.030): 0.079*"nation" + 0.038*"torah" + 0.026*"world" + 0.016*"drama" + 0.013*"commandment" + 0.012*"witness" + 0.012*"roman" + 0.011*"midrash" + 0.009*"people" + 0.008*"judgment"
2020-07-26 17:41:21,810 : INFO : topic #0 (0.030): 0.091*"death" + 0.034*"soul" + 0.023*"redemption" + 0.022*"love" + 0.021*"letter" + 0.016*"face" + 0.016*"light" + 0.015*"vision" + 0.015*"world" + 0.014*"understanding"
2020-07-26 17:41:21,811 : INFO : topic #6 (0.051): 0.061*"community" + 0.031*"rabbi" + 0.023*"political" + 0.019*"century" + 0.018*"court" + 0.016*"government" + 0.014*"authority" + 0.009*"father" + 0.009*"people" + 0.008*"city"
2020-07-26 17:41:21,812 : INFO : topic #3 (0.057): 0.045*"torah" + 0.014*"midrash" + 0.013*"scripture" + 0.013*"world" + 0.012*"rabbinic" + 0.011*"soul" + 0.010*"tradition" + 0.009*"study" + 0.009*"reading" + 0.009*"sacrifice"
2020-07-26 17:41:21,814 : INFO : topic #11 (0.072): 0.025*"woman" + 0.017*"rabbi" + 0.010*"traditi

...

2020-07-26 17:46:22,148 : INFO : topic diff=0.017032, rho=0.147442
2020-07-26 17:46:22,359 : INFO : -6.398 per-word bound, 84.3 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 17:46:22,361 : INFO : PROGRESS: pass 45, at document #30/30
2020-07-26 17:46:22,461 : INFO : optimized alpha [0.029059768, 0.037085913, 0.010067725, 0.061748043, 0.009817076, 0.009809953, 0.012611972, 0.012200007, 0.0123234885, 0.010025897, 0.022616457, 0.021525247, 0.03923315, 0.015172146, 0.06813094, 0.023529904, 0.020167442, 0.051541604, 0.009904294, 0.012361965, 0.0469386, 0.009926318, 0.009865854, 0.025655193, 0.010055922, 0.042859912, 0.04196526, 0.009755387, 0.009841903, 0.009812679]
2020-07-26 17:46:22,466 : INFO : topic #27 (0.010): 0.001*"death" + 0.001*"community" + 0.001*"world" + 0.001*"religious" + 0.001*"according" + 0.001*"rabbi" + 0.001*"torah" + 0.001*"position" + 0.001*"individual" + 0.001*"people"
2020-07-26 17:46:22,467 : INFO : topic #5 (0.010): 0.0

2020-07-26 17:46:23,806 : INFO : topic #27 (0.009): 0.001*"death" + 0.001*"community" + 0.001*"world" + 0.001*"religious" + 0.001*"according" + 0.001*"rabbi" + 0.001*"torah" + 0.001*"position" + 0.001*"individual" + 0.001*"people"
2020-07-26 17:46:23,807 : INFO : topic #17 (0.052): 0.057*"community" + 0.036*"rabbi" + 0.021*"century" + 0.021*"wife" + 0.020*"woman" + 0.020*"christian" + 0.018*"court" + 0.016*"return" + 0.015*"authority" + 0.010*"family"
2020-07-26 17:46:23,808 : INFO : topic #3 (0.062): 0.025*"people" + 0.020*"political" + 0.016*"government" + 0.015*"city" + 0.012*"community" + 0.011*"europe" + 0.010*"aviv" + 0.008*"world" + 0.008*"passage" + 0.008*"author"
2020-07-26 17:46:23,810 : INFO : topic #14 (0.070): 0.030*"death" + 0.019*"world" + 0.011*"rabbinic" + 0.010*"source" + 0.009*"according" + 0.008*"divine" + 0.008*"soul" + 0.008*"heaven" + 0.008*"century" + 0.008*"medieval"
2020-07-26 17:46:23,811 : INFO : topic diff=0.014535, rho=0.140028
2020-07-26 17:46:23,815 : IN

2020-07-26 17:46:23,855 : INFO : topic #8 (0.012): 0.029*"according" + 0.029*"talmud" + 0.029*"view" + 0.029*"meaning" + 0.029*"redemption" + 0.029*"town" + 0.029*"testament" + 0.001*"torah" + 0.001*"woman" + 0.001*"maimonides" + 0.001*"knowledge" + 0.001*"rabbi" + 0.001*"community" + 0.001*"wife" + 0.001*"faith" + 0.001*"world" + 0.001*"rabbinic" + 0.001*"people" + 0.001*"tradition" + 0.001*"fact" + 0.001*"case" + 0.001*"authority" + 0.001*"death" + 0.001*"century" + 0.001*"political" + 0.001*"discussion" + 0.001*"messianic" + 0.001*"narrative" + 0.001*"place" + 0.001*"history" + 0.001*"king" + 0.001*"study" + 0.001*"midrash" + 0.001*"passage" + 0.001*"christian" + 0.001*"source" + 0.001*"form" + 0.001*"nation" + 0.001*"matter" + 0.001*"text" + 0.001*"shall" + 0.001*"return" + 0.001*"interpretation" + 0.001*"position" + 0.001*"crown" + 0.001*"medieval" + 0.001*"question" + 0.001*"term" + 0.001*"order" + 0.001*"father"
2020-07-26 17:46:23,857 : INFO : topic #9 (0.010): 0.001*"death" + 

2020-07-26 17:46:23,871 : INFO : topic #17 (0.052): 0.057*"community" + 0.036*"rabbi" + 0.021*"century" + 0.021*"wife" + 0.020*"woman" + 0.020*"christian" + 0.018*"court" + 0.016*"return" + 0.015*"authority" + 0.010*"family" + 0.010*"case" + 0.010*"father" + 0.010*"child" + 0.009*"maimonides" + 0.008*"legal" + 0.008*"torah" + 0.007*"forced" + 0.007*"teacher" + 0.006*"leader" + 0.006*"question" + 0.006*"document" + 0.006*"teaching" + 0.005*"medieval" + 0.005*"marriage" + 0.005*"according" + 0.005*"great" + 0.005*"ruling" + 0.005*"home" + 0.005*"scholar" + 0.005*"position" + 0.005*"accepted" + 0.005*"shel" + 0.005*"sefer" + 0.005*"mother" + 0.005*"situation" + 0.005*"following" + 0.004*"aviv" + 0.004*"people" + 0.004*"work" + 0.004*"number" + 0.004*"duty" + 0.004*"city" + 0.004*"brother" + 0.004*"ritual" + 0.004*"town" + 0.004*"rabbinic" + 0.004*"place" + 0.004*"cited" + 0.004*"death" + 0.004*"matter"
2020-07-26 17:46:23,872 : INFO : topic #18 (0.009): 0.001*"death" + 0.001*"woman" + 0.0

2020-07-26 17:46:23,888 : INFO : topic #26 (0.043): 0.023*"truth" + 0.020*"religious" + 0.020*"opinion" + 0.019*"position" + 0.016*"society" + 0.015*"value" + 0.010*"belief" + 0.010*"individual" + 0.010*"ideal" + 0.010*"expression" + 0.009*"practical" + 0.009*"fact" + 0.009*"social" + 0.009*"form" + 0.007*"people" + 0.007*"community" + 0.007*"nation" + 0.007*"moral" + 0.007*"halakhic" + 0.007*"merely" + 0.007*"level" + 0.006*"attitude" + 0.006*"view" + 0.006*"consideration" + 0.006*"public" + 0.006*"different" + 0.006*"element" + 0.006*"general" + 0.006*"choice" + 0.005*"notion" + 0.005*"nature" + 0.005*"based" + 0.005*"version" + 0.005*"regard" + 0.005*"reason" + 0.005*"term" + 0.005*"regarded" + 0.005*"religion" + 0.005*"principle" + 0.005*"limit" + 0.005*"human" + 0.004*"context" + 0.004*"sense" + 0.004*"idea" + 0.004*"positive" + 0.004*"extent" + 0.004*"absolute" + 0.004*"state" + 0.004*"political" + 0.004*"common"
2020-07-26 17:46:23,890 : INFO : topic #27 (0.009): 0.001*"death" +

In [19]:
pp.pprint(validation_50p)

{   12: [   (   0,
                '0.091*"death" + 0.034*"soul" + 0.025*"redemption" + '
                '0.022*"letter" + 0.022*"love" + 0.017*"face" + 0.016*"light" '
                '+ 0.016*"vision" + 0.016*"world" + 0.015*"understanding" + '
                '0.014*"figure" + 0.013*"revelation" + 0.010*"note" + '
                '0.008*"ritual" + 0.008*"divine" + 0.007*"reader" + '
                '0.007*"human" + 0.006*"according" + 0.006*"person" + '
                '0.006*"analysis" + 0.006*"created" + 0.006*"commentary" + '
                '0.006*"describes" + 0.006*"moment" + 0.006*"reading" + '
                '0.006*"represents" + 0.005*"turn" + 0.005*"spiritual" + '
                '0.005*"ultimate" + 0.005*"goal" + 0.005*"common" + '
                '0.005*"gate" + 0.005*"final" + 0.005*"creation" + '
                '0.005*"help" + 0.005*"translation" + 0.004*"fear" + '
                '0.004*"speech" + 0.004*"suffering" + 0.004*"attention" + '
                '0.004*"ex

                '0.001*"maimonides" + 0.001*"world" + 0.001*"woman" + '
                '0.001*"revelation" + 0.001*"century" + 0.001*"wife" + '
                '0.001*"form" + 0.001*"religious" + 0.001*"nation" + '
                '0.001*"society" + 0.001*"ritual" + 0.001*"rabbi" + '
                '0.001*"fact" + 0.001*"people" + 0.001*"letter" + 0.001*"case" '
                '+ 0.001*"child" + 0.001*"opinion" + 0.001*"according" + '
                '0.001*"community" + 0.001*"light" + 0.001*"state" + '
                '0.001*"reading" + 0.001*"love" + 0.001*"rabbinic" + '
                '0.001*"term" + 0.001*"passage" + 0.001*"study" + '
                '0.001*"order" + 0.001*"truth" + 0.001*"redemption" + '
                '0.001*"tradition" + 0.001*"understanding" + 0.001*"knowledge" '
                '+ 0.001*"human" + 0.001*"vision" + 0.001*"matter" + '
                '0.001*"face" + 0.001*"interpretation" + 0.001*"position" + '
                '0.001*"individual" + 0.001*"g

                '0.001*"term" + 0.001*"sage" + 0.001*"voice" + '
                '0.001*"sacrifice" + 0.001*"nature"'),
            (   10,
                '0.062*"crown" + 0.038*"king" + 0.027*"serf" + '
                '0.022*"authority" + 0.019*"century" + 0.015*"power" + '
                '0.013*"called" + 0.013*"matter" + 0.011*"history" + '
                '0.009*"medieval" + 0.009*"political" + 0.009*"order" + '
                '0.008*"argument" + 0.008*"middle" + 0.008*"issue" + '
                '0.008*"case" + 0.008*"free" + 0.007*"state" + 0.007*"status" '
                '+ 0.007*"regard" + 0.007*"claimed" + 0.006*"joseph" + '
                '0.006*"common" + 0.006*"sense" + 0.006*"especially" + '
                '0.006*"expression" + 0.006*"holy" + 0.006*"great" + '
                '0.006*"notion" + 0.005*"idea" + 0.005*"accept" + '
                '0.005*"reaction" + 0.005*"attack" + 0.005*"relation" + '
                '0.005*"decision" + 0.005*"english" + 0.005*"making

                '0.001*"order" + 0.001*"tradition" + 0.001*"version" + '
                '0.001*"history" + 0.001*"notion" + 0.001*"great" + '
                '0.001*"individual" + 0.001*"discussion" + 0.001*"scholar" + '
                '0.001*"interpretation" + 0.001*"form" + 0.001*"suffering" + '
                '0.001*"concern" + 0.001*"true" + 0.001*"religious" + '
                '0.001*"babylonian" + 0.001*"different" + 0.001*"source" + '
                '0.001*"meaning" + 0.001*"return"'),
            (   12,
                '0.060*"maimonides" + 0.027*"suffering" + '
                '0.022*"philosophical" + 0.020*"angel" + 0.016*"reading" + '
                '0.014*"true" + 0.012*"intellectual" + 0.011*"individual" + '
                '0.011*"view" + 0.011*"understanding" + 0.010*"righteous" + '
                '0.010*"matter" + 0.009*"prayer" + 0.009*"general" + '
                '0.008*"fact" + 0.008*"according" + 0.008*"discussion" + '
                '0.008*"position" + 0.

                '0.001*"father" + 0.001*"study" + 0.001*"discussion" + '
                '0.001*"history" + 0.001*"order" + 0.001*"king" + '
                '0.001*"government" + 0.001*"return" + 0.001*"state" + '
                '0.001*"interpretation" + 0.001*"child" + 0.001*"individual" + '
                '0.001*"true" + 0.001*"authority" + 0.001*"suffering" + '
                '0.001*"example" + 0.001*"position" + 0.001*"term" + '
                '0.001*"person" + 0.001*"notion"'),
            (   25,
                '0.042*"rabbi" + 0.038*"community" + 0.029*"wife" + '
                '0.026*"court" + 0.023*"woman" + 0.016*"father" + '
                '0.016*"century" + 0.013*"maimonides" + 0.013*"authority" + '
                '0.013*"family" + 0.012*"torah" + 0.010*"teacher" + '
                '0.010*"child" + 0.009*"leader" + 0.009*"teaching" + '
                '0.008*"marriage" + 0.008*"question" + 0.007*"home" + '
                '0.007*"following" + 0.007*"aviv" + 0.007*"

In [22]:
val_models_to_check = [
    ldamodel_12t_50p_autoalpha_newtest_val,
    ldamodel_13t_50p_autoalpha_newtest_val,
    ldamodel_14t_50p_autoalpha_newtest_val,
    ldamodel_15t_50p_autoalpha_newtest_val,
    ldamodel_16t_50p_autoalpha_newtest_val,
    ldamodel_17t_50p_autoalpha_newtest_val,
    ldamodel_18t_50p_autoalpha_newtest_val,
    ldamodel_19t_50p_autoalpha_newtest_val,
    ldamodel_20t_50p_autoalpha_newtest_val,
    ldamodel_21t_50p_autoalpha_newtest_val,
    ldamodel_22t_50p_autoalpha_newtest_val,
    ldamodel_23t_50p_autoalpha_newtest_val,
    ldamodel_24t_50p_autoalpha_newtest_val,
    ldamodel_25t_50p_autoalpha_newtest_val,
    ldamodel_26t_50p_autoalpha_newtest_val,
    ldamodel_27t_50p_autoalpha_newtest_val,
    ldamodel_28t_50p_autoalpha_newtest_val,
    ldamodel_29t_50p_autoalpha_newtest_val,
    ldamodel_30t_50p_autoalpha_newtest_val,
    
    
]

In [23]:

def get_art_topics_val(val_models_to_check):
    model_num = 12
    for model in val_models_to_check:
        print('Getting art_topics_ldamodel_%dt_50p_autoalpha_val...' % (model_num))
        global art_topics_val
        art_topics_val = []
        for article in corpus:
            art_topics_val.append(model.get_document_topics(article, 
#                                            minimum_probability=0.15,   
                                           minimum_phi_value=None, 
                                           per_word_topics=False)
             )
        for i in art_topics_val:
            i.sort(key=itemgetter(1),reverse=True)
        globals()['art_topics_ldamodel_%dt_50p_autoalpha_newtest_val' % model_num] = art_topics_val
        with open('art_topics_lda_{}t_50p_autoalpha_research_val.pickle'.format(model_num),'wb') as file:
            pickle.dump(art_topics_val,file)
        print('Finished art_topics_ldamodel_%dt_50p_autoalpha_val.' % (model_num))
        model_num += 1

In [24]:
# Get the topics for each article for each model
get_art_topics_val(val_models_to_check)

Getting art_topics_ldamodel_12t_50p_autoalpha_val...
Finished art_topics_ldamodel_12t_50p_autoalpha_val.
Getting art_topics_ldamodel_13t_50p_autoalpha_val...
Finished art_topics_ldamodel_13t_50p_autoalpha_val.
Getting art_topics_ldamodel_14t_50p_autoalpha_val...
Finished art_topics_ldamodel_14t_50p_autoalpha_val.
Getting art_topics_ldamodel_15t_50p_autoalpha_val...
Finished art_topics_ldamodel_15t_50p_autoalpha_val.
Getting art_topics_ldamodel_16t_50p_autoalpha_val...
Finished art_topics_ldamodel_16t_50p_autoalpha_val.
Getting art_topics_ldamodel_17t_50p_autoalpha_val...
Finished art_topics_ldamodel_17t_50p_autoalpha_val.
Getting art_topics_ldamodel_18t_50p_autoalpha_val...
Finished art_topics_ldamodel_18t_50p_autoalpha_val.
Getting art_topics_ldamodel_19t_50p_autoalpha_val...
Finished art_topics_ldamodel_19t_50p_autoalpha_val.
Getting art_topics_ldamodel_20t_50p_autoalpha_val...
Finished art_topics_ldamodel_20t_50p_autoalpha_val.
Getting art_topics_ldamodel_21t_50p_autoalpha_val...
Fi

In [ ]:
# # Load Applied Article Topics
# for model_num in np.arange(12,21):
#     with open('pickled_files/models/noent/countvec/val/art_topics_lda_{}t_50p_autoalpha_val.pickle'.format(model_num),'rb') as file:
#         art_topics_val = pickle.load(file)
#     globals()['art_topics_ldamodel_%dt_50p_autoalpha_val' % model_num] = art_topics_val


In [26]:
applied_topics = [
    art_topics_ldamodel_12t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_13t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_14t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_15t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_16t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_17t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_18t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_19t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_20t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_21t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_22t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_23t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_24t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_25t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_26t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_27t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_28t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_29t_50p_autoalpha_newtest_val,
    art_topics_ldamodel_30t_50p_autoalpha_newtest_val,
    
]

In [27]:
def get_av_prob_scores(applied):
    applied_score = [[x[1] for x in article] for article in applied]
#     applied_score = [[x[1] for x in article if x[1]>.12] for article in applied] # --> extension to get biggest topics
    applied_score = [np.mean(article) for article in applied_score]
#     applied_score = np.sum(applied_score) # -->makes no difference with mean, but just a variation
    applied_score = np.mean(applied_score)
    return(applied_score)

In [28]:
# Get scores
scores_50p = defaultdict()
mod_num = 12
for applied in applied_topics:
    print('Getting mean average topic weights for articles in model with %d topics...' % mod_num)
    scores_50p[mod_num] = get_av_prob_scores(applied)
    mod_num += 1

# Save scores to pickle
with open('av_weight_scores_12t-20t_50p_autoalpha_countvec_research.pickle','wb') as file:
    pickle.dump(scores_50p, file)

Getting mean average topic weights for articles in model with 12 topics...
Getting mean average topic weights for articles in model with 13 topics...
Getting mean average topic weights for articles in model with 14 topics...
Getting mean average topic weights for articles in model with 15 topics...
Getting mean average topic weights for articles in model with 16 topics...
Getting mean average topic weights for articles in model with 17 topics...
Getting mean average topic weights for articles in model with 18 topics...
Getting mean average topic weights for articles in model with 19 topics...
Getting mean average topic weights for articles in model with 20 topics...
Getting mean average topic weights for articles in model with 21 topics...
Getting mean average topic weights for articles in model with 22 topics...
Getting mean average topic weights for articles in model with 23 topics...
Getting mean average topic weights for articles in model with 24 topics...
Getting mean average topi

In [ ]:
# # Load scores from pickle
# with open('pickled_files/models/noent/countvec/val/av_weight_scores_12t-20t_50p_autoalpha_countvec.pickle','rb') as file:
#     scores_50p = pickle.load(file)

In [29]:
# Which number of topics performs best with 50 passes?
scores_50p
# --> 12, which makes sense, as broader topics would have higher and less topic weights per article.
# Let's investigate and pick the lowest number of topics as possible

defaultdict(None,
            {12: 0.6171718,
             13: 0.63772446,
             14: 0.5807033,
             15: 0.51774067,
             16: 0.6483425,
             17: 0.5859002,
             18: 0.7086972,
             19: 0.56168294,
             20: 0.6014575,
             21: 0.6338871,
             22: 0.52580446,
             23: 0.54075116,
             24: 0.6945911,
             25: 0.6501845,
             26: 0.69632816,
             27: 0.6666923,
             28: 0.58848447,
             29: 0.5865671,
             30: 0.5155598})

In [ ]:

art_topics_ldamodel_12t_50p_autoalpha_book_val

In [30]:
# Dictionary to store topics in
validation_200p = {}
# Function to calculate and store models for validating choice for no_of_topics
def cross_val_topics_200p(no_of_topics):
    model = LdaModel(corpus, num_topics=no_of_topics, id2word = dictionary, passes=200, alpha='auto', eval_every=2000)
    globals()['ldamodel_%dt_200p_autoalpha_research_val' % no_of_topics] = model
    model.save('lda_{}t_200p_autoalpha_research_val.model'.format(no_of_topics))
    validation_200p[no_of_topics] = model.print_topics(num_topics=-1, num_words=50)

In [36]:
# Loop through x-x topics to see optimal number of topics
for i in np.arange(16,19):
    print('Running LDA with 200 passes for {} topics...'.format(i))
    cross_val_topics_200p(i)
    with open('dict_topics_from_validation_research_200p.pickle', 'wb') as file:
        pickle.dump(validation_200p, file)

2020-07-26 19:16:08,256 : INFO : using autotuned alpha, starting with [0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625]
2020-07-26 19:16:08,257 : INFO : using symmetric eta at 0.0625
2020-07-26 19:16:08,258 : INFO : using serial LDA version on this node
2020-07-26 19:16:08,262 : INFO : running online (multi-pass) LDA training, 16 topics, 200 passes over the supplied corpus of 30 documents, updating model once every 30 documents, evaluating perplexity every 30 documents, iterating 50x with a convergence threshold of 0.001000
2020-07-26 19:16:08,429 : INFO : -7.741 per-word bound, 214.0 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 19:16:08,431 : INFO : PROGRESS: pass 0, at document #30/30


Running LDA with 200 passes for 16 topics...


2020-07-26 19:16:08,484 : INFO : optimized alpha [0.10804537, 0.105995536, 0.10386145, 0.10984105, 0.10409527, 0.10415608, 0.104554154, 0.10481486, 0.104155384, 0.105329484, 0.10320355, 0.10036212, 0.10828036, 0.107014745, 0.10529418, 0.104434684]
2020-07-26 19:16:08,487 : INFO : topic #11 (0.100): 0.014*"maimonides" + 0.013*"torah" + 0.008*"midrash" + 0.008*"woman" + 0.008*"nation" + 0.007*"rabbinic" + 0.007*"rabbi" + 0.007*"narrative" + 0.005*"people" + 0.005*"passage"
2020-07-26 19:16:08,488 : INFO : topic #10 (0.103): 0.012*"death" + 0.010*"community" + 0.007*"century" + 0.006*"people" + 0.006*"position" + 0.006*"religious" + 0.006*"opinion" + 0.006*"maimonides" + 0.005*"torah" + 0.005*"rabbinic"
2020-07-26 19:16:08,489 : INFO : topic #0 (0.108): 0.012*"maimonides" + 0.010*"death" + 0.008*"dead" + 0.008*"torah" + 0.008*"world" + 0.006*"story" + 0.006*"rabbi" + 0.006*"place" + 0.006*"father" + 0.006*"woman"
2020-07-26 19:16:08,490 : INFO : topic #12 (0.108): 0.017*"death" + 0.016*"t

2020-07-26 19:16:09,472 : INFO : topic #11 (0.032): 0.009*"maimonides" + 0.008*"torah" + 0.006*"midrash" + 0.005*"woman" + 0.005*"nation" + 0.005*"narrative" + 0.005*"rabbinic" + 0.005*"rabbi" + 0.004*"people" + 0.004*"passage"
2020-07-26 19:16:09,473 : INFO : topic #14 (0.037): 0.046*"literature" + 0.032*"form" + 0.029*"kind" + 0.020*"literary" + 0.016*"mode" + 0.015*"history" + 0.015*"criticism" + 0.011*"annual" + 0.011*"joseph" + 0.010*"begin"
2020-07-26 19:16:09,474 : INFO : topic #12 (0.055): 0.067*"torah" + 0.021*"soul" + 0.018*"rabbinic" + 0.018*"sacrifice" + 0.013*"tradition" + 0.012*"food" + 0.011*"ritual" + 0.011*"study" + 0.009*"medieval" + 0.009*"israelite"
2020-07-26 19:16:09,475 : INFO : topic #9 (0.057): 0.049*"woman" + 0.030*"rabbi" + 0.025*"wife" + 0.016*"babylonian" + 0.016*"tradition" + 0.016*"text" + 0.015*"story" + 0.012*"rabbinic" + 0.012*"talmud" + 0.008*"scholar"
2020-07-26 19:16:09,476 : INFO : topic #1 (0.069): 0.036*"death" + 0.016*"world" + 0.012*"people" + 

2020-07-26 19:16:10,580 : INFO : topic #11 (0.022): 0.003*"maimonides" + 0.003*"torah" + 0.002*"midrash" + 0.002*"woman" + 0.002*"nation" + 0.002*"narrative" + 0.002*"rabbinic" + 0.002*"rabbi" + 0.002*"people" + 0.002*"passage"
2020-07-26 19:16:10,582 : INFO : topic #14 (0.027): 0.073*"literature" + 0.045*"form" + 0.045*"kind" + 0.030*"literary" + 0.023*"mode" + 0.023*"history" + 0.023*"criticism" + 0.020*"annual" + 0.015*"joseph" + 0.015*"begin"
2020-07-26 19:16:10,583 : INFO : topic #9 (0.045): 0.053*"woman" + 0.033*"rabbi" + 0.027*"wife" + 0.017*"text" + 0.017*"tradition" + 0.016*"babylonian" + 0.015*"story" + 0.013*"rabbinic" + 0.013*"talmud" + 0.008*"sexual"
2020-07-26 19:16:10,584 : INFO : topic #8 (0.047): 0.049*"community" + 0.024*"christian" + 0.020*"century" + 0.016*"return" + 0.016*"rabbi" + 0.013*"government" + 0.012*"political" + 0.011*"authority" + 0.010*"medieval" + 0.009*"case"
2020-07-26 19:16:10,585 : INFO : topic #1 (0.056): 0.039*"death" + 0.016*"world" + 0.013*"peo

...

2020-07-26 19:19:07,421 : INFO : topic #4 (0.079): 0.051*"torah" + 0.033*"nation" + 0.017*"rabbinic" + 0.015*"world" + 0.014*"medieval" + 0.013*"sacrifice" + 0.011*"soul" + 0.010*"biblical" + 0.010*"tradition" + 0.009*"people"
2020-07-26 19:19:07,422 : INFO : topic #12 (0.087): 0.053*"woman" + 0.033*"rabbi" + 0.023*"wife" + 0.017*"tradition" + 0.016*"text" + 0.014*"rabbinic" + 0.013*"talmud" + 0.010*"example" + 0.009*"babylonian" + 0.008*"source"
2020-07-26 19:19:07,423 : INFO : topic diff=0.002237, rho=0.072932
2020-07-26 19:19:07,606 : INFO : -6.349 per-word bound, 81.5 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 19:19:07,607 : INFO : PROGRESS: pass 187, at document #30/30
2020-07-26 19:19:07,660 : INFO : optimized alpha [0.0047590532, 0.004845792, 0.01030123, 0.024096051, 0.079258785, 0.040071443, 0.0047688233, 0.06828206, 0.0541357, 0.004776871, 0.06897716, 0.046557363, 0.087518305, 0.0047729025, 0.007210819, 0.030548679, 0.023534823, 

2020-07-26 19:19:08,629 : INFO : topic #10 (0.070): 0.018*"society" + 0.018*"religious" + 0.016*"truth" + 0.016*"opinion" + 0.016*"position" + 0.013*"individual" + 0.011*"value" + 0.010*"fact" + 0.009*"ideal" + 0.009*"social"
2020-07-26 19:19:08,631 : INFO : topic #4 (0.079): 0.051*"torah" + 0.033*"nation" + 0.017*"rabbinic" + 0.015*"world" + 0.014*"medieval" + 0.013*"sacrifice" + 0.011*"soul" + 0.010*"biblical" + 0.010*"tradition" + 0.009*"people"
2020-07-26 19:19:08,633 : INFO : topic #12 (0.087): 0.053*"woman" + 0.033*"rabbi" + 0.023*"wife" + 0.017*"tradition" + 0.016*"text" + 0.014*"rabbinic" + 0.013*"talmud" + 0.010*"example" + 0.009*"babylonian" + 0.008*"source"
2020-07-26 19:19:08,634 : INFO : topic diff=0.002097, rho=0.071982
2020-07-26 19:19:08,889 : INFO : -6.349 per-word bound, 81.5 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 19:19:08,890 : INFO : PROGRESS: pass 192, at document #30/30
2020-07-26 19:19:08,968 : INFO : optimized 

2020-07-26 19:19:09,979 : INFO : topic #0 (0.005): 0.001*"phrase" + 0.001*"philosophical" + 0.001*"pious" + 0.001*"picture" + 0.001*"physical" + 0.001*"placed" + 0.001*"philosophy" + 0.001*"personal" + 0.001*"perspective" + 0.001*"pointed"
2020-07-26 19:19:09,980 : INFO : topic #10 (0.070): 0.018*"society" + 0.018*"religious" + 0.016*"truth" + 0.016*"opinion" + 0.016*"position" + 0.013*"individual" + 0.011*"value" + 0.010*"fact" + 0.009*"ideal" + 0.009*"social"
2020-07-26 19:19:09,981 : INFO : topic #4 (0.079): 0.051*"torah" + 0.034*"nation" + 0.017*"rabbinic" + 0.015*"world" + 0.014*"medieval" + 0.013*"sacrifice" + 0.011*"soul" + 0.010*"biblical" + 0.010*"tradition" + 0.009*"people"
2020-07-26 19:19:09,981 : INFO : topic #12 (0.088): 0.053*"woman" + 0.033*"rabbi" + 0.023*"wife" + 0.017*"tradition" + 0.016*"text" + 0.014*"rabbinic" + 0.013*"talmud" + 0.010*"example" + 0.009*"babylonian" + 0.008*"source"
2020-07-26 19:19:09,982 : INFO : topic diff=0.001956, rho=0.071067
2020-07-26 19:19

2020-07-26 19:19:10,824 : INFO : topic #2 (0.010): 0.029*"document" + 0.029*"town" + 0.029*"egypt" + 0.015*"rule" + 0.015*"imply" + 0.015*"government" + 0.015*"foundation" + 0.015*"mind" + 0.015*"pious" + 0.015*"history" + 0.015*"self" + 0.015*"medieval" + 0.015*"literature" + 0.015*"redemption" + 0.015*"view" + 0.015*"meaning" + 0.015*"testament" + 0.015*"according" + 0.015*"talmud" + 0.001*"philosophical" + 0.001*"particularly" + 0.001*"past" + 0.001*"order" + 0.001*"particular" + 0.001*"origin" + 0.001*"original" + 0.001*"possibility" + 0.001*"overcome" + 0.001*"paradigm" + 0.001*"parallel" + 0.001*"party" + 0.001*"pattern" + 0.001*"outside" + 0.001*"philosophy" + 0.001*"physical" + 0.001*"picture" + 0.001*"passage" + 0.001*"place" + 0.001*"placed" + 0.001*"play" + 0.001*"pointed" + 0.001*"political" + 0.001*"poor" + 0.001*"popular" + 0.001*"portion" + 0.001*"position" + 0.001*"positive" + 0.001*"personal" + 0.001*"phrase" + 0.001*"philosopher"
2020-07-26 19:19:10,827 : INFO : topic

2020-07-26 19:19:10,846 : INFO : topic #11 (0.047): 0.042*"death" + 0.021*"people" + 0.017*"soul" + 0.014*"world" + 0.013*"love" + 0.012*"letter" + 0.012*"city" + 0.011*"redemption" + 0.011*"aviv" + 0.010*"reader" + 0.010*"figure" + 0.009*"light" + 0.008*"face" + 0.008*"vision" + 0.008*"land" + 0.007*"trans" + 0.007*"europe" + 0.007*"understanding" + 0.006*"author" + 0.006*"great" + 0.006*"note" + 0.006*"father" + 0.006*"battle" + 0.006*"place" + 0.006*"memory" + 0.006*"young" + 0.006*"gate" + 0.006*"dead" + 0.006*"order" + 0.006*"person" + 0.005*"revelation" + 0.005*"blood" + 0.005*"voice" + 0.005*"brother" + 0.005*"encounter" + 0.005*"mother" + 0.005*"divine" + 0.005*"suffering" + 0.005*"reading" + 0.005*"human" + 0.004*"translation" + 0.004*"literature" + 0.004*"experience" + 0.004*"according" + 0.004*"english" + 0.004*"turn" + 0.004*"collection" + 0.004*"goal" + 0.004*"fear" + 0.004*"word"
2020-07-26 19:19:10,850 : INFO : topic #12 (0.087): 0.053*"woman" + 0.033*"rabbi" + 0.023*"wi

In [ ]:
# # Load Models
# for no_of_topics in np.arange(12,17):
#     model =  models.LdaModel.load('lda_{}t_200p_autoalpha_val.model'.format(no_of_topics))
#     globals()['ldamodel_%dt_200p_autoalpha_val' % no_of_topics] = model
# # Load Validation Topics 
# with open('dict_topics_from_validation_200p.pickle', 'rb') as file:
#     validation_200p = pickle.load(file)

In [37]:
pp.pprint(validation_200p)

{   16: [   (   0,
                '0.031*"spirit" + 0.028*"revelation" + 0.027*"state" + '
                '0.016*"case" + 0.016*"rabbi" + 0.012*"prophet" + '
                '0.012*"experience" + 0.011*"cultural" + 0.011*"society" + '
                '0.011*"speech" + 0.010*"century" + 0.010*"study" + '
                '0.010*"prophecy" + 0.009*"ritual" + 0.008*"voice" + '
                '0.008*"angel" + 0.008*"term" + 0.007*"joseph" + 0.007*"form" '
                '+ 0.007*"positive" + 0.007*"self" + 0.006*"female" + '
                '0.006*"fact" + 0.006*"based" + 0.006*"individual" + '
                '0.006*"behavior" + 0.006*"woman" + 0.006*"appears" + '
                '0.006*"contrast" + 0.006*"mouth" + 0.006*"context" + '
                '0.005*"speaking" + 0.005*"identity" + 0.005*"encounter" + '
                '0.005*"soul" + 0.005*"theory" + 0.005*"model" + 0.005*"level" '
                '+ 0.005*"association" + 0.005*"source" + 0.005*"movement" + '
                '0

In [38]:
val_models_to_check = [
    ldamodel_16t_200p_autoalpha_research_val,
    ldamodel_17t_200p_autoalpha_research_val,
     ldamodel_18t_200p_autoalpha_research_val,
#     ldamodel_15t_200p_autoalpha_book_val,
#     ldamodel_16t_200p_autoalpha_book_val,
     
     
]

In [42]:
def get_art_topics_val(val_models_to_check):
    model_num = 16
    for model in val_models_to_check:
        print('Getting art_topics_ldamodel_%dt_200p_autoalpha_research_val...' % (model_num))
        global art_topics_val
        art_topics_val = []
        for article in corpus:
            art_topics_val.append(model.get_document_topics(article, 
#                                            minimum_probability=0.15,   
                                           minimum_phi_value=None, 
                                           per_word_topics=False)
             )
        for i in art_topics_val:
            i.sort(key=itemgetter(1),reverse=True)
        globals()['art_topics_ldamodel_%dt_200p_autoalpha_research_val' % model_num] = art_topics_val
        with open('art_topics_lda_{}t_200p_autoalpha_research_val.pickle'.format(model_num),'wb') as file:
            pickle.dump(art_topics_val,file)
        print('Finished art_topics_ldamodel_%dt_200p_autoalpha_research_val.' % (model_num))
        model_num += 1

In [43]:
get_art_topics_val(val_models_to_check)

Getting art_topics_ldamodel_16t_200p_autoalpha_research_val...
Finished art_topics_ldamodel_16t_200p_autoalpha_research_val.
Getting art_topics_ldamodel_17t_200p_autoalpha_research_val...
Finished art_topics_ldamodel_17t_200p_autoalpha_research_val.
Getting art_topics_ldamodel_18t_200p_autoalpha_research_val...
Finished art_topics_ldamodel_18t_200p_autoalpha_research_val.


In [ ]:
# # Load Article Topics
# for model_num in np.arange(12,17):
#     with open('pickled_files/models/noent/countvec/val/art_topics_lda_{}t_200p_autoalpha_val.pickle'.format(model_num),'rb') as file:
#           art_topics_val = pickle.load(file)
#     globals()['art_topics_ldamodel_%dt_200p_autoalpha_val' % model_num] = art_topics_val

In [44]:
applied_topics = [  
    art_topics_ldamodel_16t_200p_autoalpha_research_val,
    art_topics_ldamodel_17t_200p_autoalpha_research_val,
    art_topics_ldamodel_18t_200p_autoalpha_research_val,
    
     
]

In [45]:
def get_av_prob_scores(applied):
    applied_score = [[x[1] for x in article[:5]] for article in applied]
#     applied_score = [[x[1] for x in article if x[1]>.12] for article in applied] # --> extension to get biggest topics
    applied_score = [np.mean(article) for article in applied_score]
#     applied_score = np.sum(applied_score) # -->makes no difference with mean, but just a variation
    applied_score = np.mean(applied_score)
    return(applied_score)

In [46]:
# Get scores
scores_200p = defaultdict()
mod_num = 16
for applied in applied_topics:
    print('Getting mean average topic weights for articles in model with %d topics...' % mod_num)
    scores_200p[mod_num] = get_av_prob_scores(applied)
    mod_num += 1

# Save scores to pickle
with open('av_weight_scores_16t-18t_200p_autoalpha_countvec_research.pickle','wb') as file:
    pickle.dump(scores_200p,file)

Getting mean average topic weights for articles in model with 16 topics...
Getting mean average topic weights for articles in model with 17 topics...
Getting mean average topic weights for articles in model with 18 topics...


In [ ]:
# # Load scores from pickle
# with open('pickled_files/models/noent/countvec/val/av_weight_scores_12t-16t_200p_autoalpha_countvec.pickle','rb') as file:
#     scores_200p = pickle.load(file)

In [47]:
# Which number of topics performs best with 200 passes?
scores_200p

# Even though 15 seems best, running the model for 300 passes for both 14 and 15 topics, 
# 14 topics resulted in the most distinct topics. Therefore, I went with that model.

defaultdict(None, {16: 0.62391627, 17: 0.5286459, 18: 0.508111})

In [48]:
# Run Model (12)
no_of_topics = 16
ldamodel16 = LdaModel(corpus, num_topics=no_of_topics, id2word = dictionary, passes=300, alpha='auto', eval_every=2000)
# Save Model (24)
ldamodel16.save('lda_{}t_300p_autoalpha_research_val.model'.format(no_of_topics))

2020-07-26 19:23:46,640 : INFO : using autotuned alpha, starting with [0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625]
2020-07-26 19:23:46,642 : INFO : using symmetric eta at 0.0625
2020-07-26 19:23:46,644 : INFO : using serial LDA version on this node
2020-07-26 19:23:46,647 : INFO : running online (multi-pass) LDA training, 16 topics, 300 passes over the supplied corpus of 30 documents, updating model once every 30 documents, evaluating perplexity every 30 documents, iterating 50x with a convergence threshold of 0.001000
2020-07-26 19:23:46,847 : INFO : -7.740 per-word bound, 213.8 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 19:23:46,848 : INFO : PROGRESS: pass 0, at document #30/30
2020-07-26 19:23:46,901 : INFO : optimized alpha [0.10397184, 0.10152513, 0.10492568, 0.103345856, 0.105188414, 0.10751583, 0.10790896, 0.103584565, 0.10485149, 0.10242228, 0.1091

2020-07-26 19:23:48,146 : INFO : topic #11 (0.068): 0.017*"knowledge" + 0.014*"revelation" + 0.013*"faith" + 0.011*"spirit" + 0.011*"state" + 0.010*"messianic" + 0.010*"rabbi" + 0.008*"tradition" + 0.008*"rabbinic" + 0.007*"people"
2020-07-26 19:23:48,148 : INFO : topic #4 (0.070): 0.034*"nation" + 0.029*"torah" + 0.015*"narrative" + 0.013*"world" + 0.013*"midrash" + 0.012*"political" + 0.011*"people" + 0.010*"babylonian" + 0.009*"shall" + 0.009*"rabbi"
2020-07-26 19:23:48,149 : INFO : topic diff=0.566143, rho=0.408248
2020-07-26 19:23:48,373 : INFO : -6.489 per-word bound, 89.8 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 19:23:48,375 : INFO : PROGRESS: pass 5, at document #30/30
2020-07-26 19:23:48,434 : INFO : optimized alpha [0.03692704, 0.04747942, 0.062226925, 0.040730692, 0.066787064, 0.043630548, 0.03795941, 0.04894728, 0.03742719, 0.03370951, 0.057887528, 0.06249693, 0.05576949, 0.042905368, 0.062762074, 0.043745626]
2020-07-26 19:

2020-07-26 19:23:49,907 : INFO : topic #4 (0.059): 0.035*"nation" + 0.030*"torah" + 0.016*"narrative" + 0.014*"world" + 0.014*"midrash" + 0.012*"political" + 0.010*"shall" + 0.010*"people" + 0.010*"babylonian" + 0.009*"story"
2020-07-26 19:23:49,908 : INFO : topic #14 (0.059): 0.054*"community" + 0.031*"rabbi" + 0.020*"century" + 0.020*"christian" + 0.014*"court" + 0.014*"return" + 0.012*"authority" + 0.008*"death" + 0.008*"father" + 0.008*"case"
2020-07-26 19:23:49,909 : INFO : topic diff=0.467849, rho=0.301511
2020-07-26 19:23:50,088 : INFO : -6.387 per-word bound, 83.7 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 19:23:50,089 : INFO : PROGRESS: pass 10, at document #30/30
2020-07-26 19:23:50,117 : INFO : optimized alpha [0.025920598, 0.043898538, 0.0540704, 0.030181387, 0.057455238, 0.030360578, 0.02617998, 0.043995623, 0.024617683, 0.023006178, 0.04949772, 0.04843481, 0.04191692, 0.033398595, 0.058365107, 0.03793616]
2020-07-26 19:23:50

2020-07-26 19:23:51,012 : INFO : topic #4 (0.054): 0.034*"nation" + 0.030*"torah" + 0.016*"narrative" + 0.015*"world" + 0.014*"midrash" + 0.012*"political" + 0.011*"shall" + 0.010*"people" + 0.010*"babylonian" + 0.009*"story"
2020-07-26 19:23:51,014 : INFO : topic #14 (0.056): 0.052*"community" + 0.030*"rabbi" + 0.020*"century" + 0.019*"christian" + 0.014*"court" + 0.014*"return" + 0.012*"authority" + 0.008*"case" + 0.008*"father" + 0.008*"death"
2020-07-26 19:23:51,015 : INFO : topic diff=0.204498, rho=0.250000
2020-07-26 19:23:51,187 : INFO : -6.362 per-word bound, 82.2 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 19:23:51,188 : INFO : PROGRESS: pass 15, at document #30/30
2020-07-26 19:23:51,238 : INFO : optimized alpha [0.021621486, 0.041954443, 0.05054228, 0.025859384, 0.053027928, 0.024797242, 0.021098733, 0.042023625, 0.019274253, 0.018283116, 0.048946623, 0.04142588, 0.03578971, 0.03043963, 0.055912588, 0.033743497]
2020-07-26 19:23

2020-07-26 19:23:52,296 : INFO : topic #4 (0.051): 0.034*"nation" + 0.031*"torah" + 0.016*"narrative" + 0.015*"world" + 0.014*"midrash" + 0.011*"political" + 0.011*"shall" + 0.010*"people" + 0.009*"babylonian" + 0.009*"story"
2020-07-26 19:23:52,297 : INFO : topic #14 (0.054): 0.051*"community" + 0.029*"rabbi" + 0.020*"century" + 0.019*"christian" + 0.014*"court" + 0.013*"return" + 0.012*"authority" + 0.008*"case" + 0.008*"father" + 0.008*"death"
2020-07-26 19:23:52,298 : INFO : topic diff=0.083700, rho=0.218218
2020-07-26 19:23:52,497 : INFO : -6.354 per-word bound, 81.8 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 19:23:52,498 : INFO : PROGRESS: pass 20, at document #30/30
2020-07-26 19:23:52,588 : INFO : optimized alpha [0.01932429, 0.040636536, 0.048325628, 0.023417864, 0.0503629, 0.021601068, 0.018144693, 0.04064121, 0.016213097, 0.015509893, 0.04868665, 0.03721551, 0.032319352, 0.029425235, 0.05410141, 0.030799389]
2020-07-26 19:23:52

...

2020-07-26 19:25:03,040 : INFO : PROGRESS: pass 280, at document #30/30
2020-07-26 19:25:03,082 : INFO : optimized alpha [0.006344165, 0.035806127, 0.041025005, 0.016466783, 0.04554652, 0.00902158, 0.0058219056, 0.03407028, 0.0035966556, 0.0035613745, 0.0582306, 0.025292369, 0.02711161, 0.024553053, 0.05793026, 0.029099364]
2020-07-26 19:25:03,086 : INFO : topic #8 (0.004): 0.001*"phrase" + 0.001*"philosophical" + 0.001*"pious" + 0.001*"picture" + 0.001*"physical" + 0.001*"placed" + 0.001*"philosophy" + 0.001*"personal" + 0.001*"perspective" + 0.001*"pointed"
2020-07-26 19:25:03,088 : INFO : topic #9 (0.004): 0.001*"phrase" + 0.001*"philosophical" + 0.001*"pious" + 0.001*"picture" + 0.001*"physical" + 0.001*"placed" + 0.001*"philosophy" + 0.001*"personal" + 0.001*"perspective" + 0.001*"pointed"
2020-07-26 19:25:03,089 : INFO : topic #4 (0.046): 0.039*"nation" + 0.035*"torah" + 0.019*"narrative" + 0.017*"midrash" + 0.016*"world" + 0.013*"shall" + 0.011*"story" + 0.010*"babylonian" + 0.0

2020-07-26 19:25:04,015 : INFO : topic diff=0.000931, rho=0.059131
2020-07-26 19:25:04,182 : INFO : -6.332 per-word bound, 80.5 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 19:25:04,183 : INFO : PROGRESS: pass 285, at document #30/30
2020-07-26 19:25:04,237 : INFO : optimized alpha [0.0063033514, 0.035844438, 0.041035563, 0.016459448, 0.04551173, 0.008996338, 0.005790574, 0.034076154, 0.0035626106, 0.003527992, 0.05827633, 0.02529327, 0.02729382, 0.02455124, 0.05815526, 0.029143406]
2020-07-26 19:25:04,241 : INFO : topic #9 (0.004): 0.001*"phrase" + 0.001*"philosophical" + 0.001*"pious" + 0.001*"picture" + 0.001*"physical" + 0.001*"placed" + 0.001*"philosophy" + 0.001*"personal" + 0.001*"perspective" + 0.001*"pointed"
2020-07-26 19:25:04,242 : INFO : topic #8 (0.004): 0.001*"phrase" + 0.001*"philosophical" + 0.001*"pious" + 0.001*"picture" + 0.001*"physical" + 0.001*"placed" + 0.001*"philosophy" + 0.001*"personal" + 0.001*"perspective" + 0.

2020-07-26 19:25:05,247 : INFO : topic #14 (0.058): 0.049*"community" + 0.027*"rabbi" + 0.020*"century" + 0.019*"christian" + 0.013*"return" + 0.013*"court" + 0.013*"political" + 0.013*"authority" + 0.010*"government" + 0.008*"people"
2020-07-26 19:25:05,249 : INFO : topic diff=0.000911, rho=0.058621
2020-07-26 19:25:05,455 : INFO : -6.332 per-word bound, 80.5 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 19:25:05,455 : INFO : PROGRESS: pass 290, at document #30/30
2020-07-26 19:25:05,489 : INFO : optimized alpha [0.006263834, 0.035809983, 0.04104673, 0.01645262, 0.04557158, 0.008972019, 0.0057601775, 0.034081742, 0.0035295037, 0.0034955232, 0.05832258, 0.02529478, 0.027488433, 0.024559349, 0.058365293, 0.029185172]
2020-07-26 19:25:05,493 : INFO : topic #9 (0.003): 0.001*"phrase" + 0.001*"philosophical" + 0.001*"pious" + 0.001*"picture" + 0.001*"physical" + 0.001*"placed" + 0.001*"philosophy" + 0.001*"personal" + 0.001*"perspective" + 0.001

2020-07-26 19:25:06,513 : INFO : topic #10 (0.058): 0.020*"torah" + 0.020*"world" + 0.014*"scripture" + 0.014*"tradition" + 0.014*"reading" + 0.014*"biblical" + 0.009*"interpretation" + 0.009*"rabbinic" + 0.009*"text" + 0.009*"result"
2020-07-26 19:25:06,515 : INFO : topic #14 (0.059): 0.049*"community" + 0.027*"rabbi" + 0.020*"century" + 0.019*"christian" + 0.013*"return" + 0.013*"court" + 0.013*"political" + 0.013*"authority" + 0.010*"government" + 0.008*"people"
2020-07-26 19:25:06,516 : INFO : topic diff=0.000893, rho=0.058124
2020-07-26 19:25:06,739 : INFO : -6.331 per-word bound, 80.5 perplexity estimate based on a held-out corpus of 30 documents with 49140 words
2020-07-26 19:25:06,740 : INFO : PROGRESS: pass 295, at document #30/30
2020-07-26 19:25:06,786 : INFO : optimized alpha [0.0062255254, 0.035778776, 0.041057453, 0.016446337, 0.045625746, 0.008948529, 0.0057306513, 0.034086622, 0.003497285, 0.00346392, 0.058366504, 0.025296444, 0.02765323, 0.024556184, 0.058557782, 0.029

2020-07-26 19:25:07,951 : INFO : topic #4 (0.046): 0.039*"nation" + 0.036*"torah" + 0.019*"narrative" + 0.017*"midrash" + 0.016*"world" + 0.014*"shall" + 0.011*"story" + 0.011*"babylonian" + 0.010*"version" + 0.009*"joshua"
2020-07-26 19:25:07,953 : INFO : topic #10 (0.058): 0.020*"torah" + 0.020*"world" + 0.014*"scripture" + 0.014*"reading" + 0.014*"tradition" + 0.014*"biblical" + 0.009*"interpretation" + 0.009*"rabbinic" + 0.009*"text" + 0.009*"result"
2020-07-26 19:25:07,954 : INFO : topic #14 (0.059): 0.049*"community" + 0.027*"rabbi" + 0.020*"century" + 0.019*"christian" + 0.013*"return" + 0.013*"court" + 0.013*"political" + 0.013*"authority" + 0.010*"government" + 0.008*"people"
2020-07-26 19:25:07,955 : INFO : topic diff=0.000878, rho=0.057639
2020-07-26 19:25:07,960 : INFO : saving LdaState object under lda_16t_300p_autoalpha_research_val.model.state, separately None
2020-07-26 19:25:07,964 : INFO : saved lda_16t_300p_autoalpha_research_val.model.state
2020-07-26 19:25:07,980 :

In [ ]:
# # Load Model
# no_of_topics = 14
ldamodel17 = LdaModel.load('lda_17t_50p_autoalpha_book_val.model')

In [49]:
## Print Topics (14)
ldamodel16.print_topics(num_topics=-1, num_words=10)

2020-07-26 19:27:04,175 : INFO : topic #0 (0.006): 0.060*"crown" + 0.037*"king" + 0.027*"serf" + 0.022*"authority" + 0.019*"century" + 0.015*"power" + 0.013*"matter" + 0.013*"called" + 0.011*"history" + 0.009*"political"
2020-07-26 19:27:04,177 : INFO : topic #1 (0.036): 0.076*"woman" + 0.037*"rabbi" + 0.037*"wife" + 0.022*"tradition" + 0.021*"text" + 0.018*"talmud" + 0.017*"rabbinic" + 0.016*"babylonian" + 0.015*"story" + 0.012*"sexual"
2020-07-26 19:27:04,178 : INFO : topic #2 (0.041): 0.019*"opinion" + 0.018*"truth" + 0.017*"religious" + 0.016*"position" + 0.015*"society" + 0.012*"value" + 0.011*"individual" + 0.011*"belief" + 0.010*"ideal" + 0.009*"fact"
2020-07-26 19:27:04,180 : INFO : topic #3 (0.016): 0.035*"people" + 0.019*"city" + 0.017*"aviv" + 0.012*"land" + 0.012*"father" + 0.011*"europe" + 0.011*"reader" + 0.011*"world" + 0.010*"death" + 0.010*"trans"
2020-07-26 19:27:04,181 : INFO : topic #4 (0.046): 0.039*"nation" + 0.036*"torah" + 0.019*"narrative" + 0.017*"midrash" + 0

[(0,
  '0.060*"crown" + 0.037*"king" + 0.027*"serf" + 0.022*"authority" + 0.019*"century" + 0.015*"power" + 0.013*"matter" + 0.013*"called" + 0.011*"history" + 0.009*"political"'),
 (1,
  '0.076*"woman" + 0.037*"rabbi" + 0.037*"wife" + 0.022*"tradition" + 0.021*"text" + 0.018*"talmud" + 0.017*"rabbinic" + 0.016*"babylonian" + 0.015*"story" + 0.012*"sexual"'),
 (2,
  '0.019*"opinion" + 0.018*"truth" + 0.017*"religious" + 0.016*"position" + 0.015*"society" + 0.012*"value" + 0.011*"individual" + 0.011*"belief" + 0.010*"ideal" + 0.009*"fact"'),
 (3,
  '0.035*"people" + 0.019*"city" + 0.017*"aviv" + 0.012*"land" + 0.012*"father" + 0.011*"europe" + 0.011*"reader" + 0.011*"world" + 0.010*"death" + 0.010*"trans"'),
 (4,
  '0.039*"nation" + 0.036*"torah" + 0.019*"narrative" + 0.017*"midrash" + 0.016*"world" + 0.014*"shall" + 0.011*"story" + 0.011*"babylonian" + 0.010*"version" + 0.009*"joshua"'),
 (5,
  '0.052*"maimonides" + 0.035*"midrash" + 0.015*"meaning" + 0.014*"matter" + 0.012*"prophet" +

In [ ]:
# Print Topics (14)
ldamodel14.show_topics(num_topics=-1, num_words=5, formatted=False)

In [ ]:
# Save Topics
final_topics1 = ldamodel14.print_topics(num_topics=-1, num_words=50)
with open('dict_topics_from_final_model_12t_200p_book.pickle', 'wb') as file:
        pickle.dump(final_topics14, file)

In [ ]:
pp.pprint(ldamodel14.show_topics(num_topics=-1, num_words=50, formatted=False))

In [ ]:
#You determine these. Each topic should have a label.

topics = {
    0: 'rabbinic',
    1: 'nineteenth',
    2: 'holocaust',
    3: 'medieval',
    4: 'bible',
    5: 'sephardic',
    6: 'sources',
    7: 'philosophy',
    8: 'gender',
    9: 'america',
    10: 'yiddish',
    11: 'kabbalah',
    
}

In [ ]:
rabbinic = ldamodel14.show_topics(num_topics=-1, num_words=50)[0][1].split()

rabbinic_words = []
for word in np.arange(0,len(rabbinic))[::2]:
    rabbinic_words.append(int(float(rabbinic[word].split('*')[0])*1000)*[rabbinic[word].split('*')[1].split('"')[1]])
# rabbinic_words

In [ ]:
rabbinic_words

In [ ]:
nineteenth = ldamodel14.show_topics(num_topics=-1, num_words=50)[1][1].split()
nineteenth_words = []
for word in np.arange(0,len(nineteenth))[::2]:
    nineteenth_words.append(int(float(nineteenth[word].split('*')[0])*1000)*[nineteenth[word].split('*')[1].split('"')[1]])
# nineteenth_words


In [ ]:
nineteenth_words

In [ ]:
holocaust = ldamodel14.show_topics(num_topics=-1, num_words=50)[2][1].split()
holocaust_words = []
for word in np.arange(0,len(holocaust))[::2]:
    holocaust_words.append(int(float(holocaust[word].split('*')[0])*1000)*[holocaust[word].split('*')[1].split('"')[1]])
# holocaust_words

In [ ]:
medieval = ldamodel14.show_topics(num_topics=-1, num_words=50)[3][1].split()
medieval_words = []
for word in np.arange(0,len(medieval))[::2]:
    medieval_words.append(int(float(medieval[word].split('*')[0])*1000)*[medieval[word].split('*')[1].split('"')[1]])
# medieval_words


In [ ]:
bible = ldamodel14.show_topics(num_topics=-1, num_words=50)[4][1].split()
bible_words = []
for word in np.arange(0,len(bible))[::2]:
    bible_words.append(int(float(bible[word].split('*')[0])*1000)*[bible[word].split('*')[1].split('"')[1]])
#bible_words

In [ ]:
sephardic = ldamodel14.show_topics(num_topics=-1, num_words=50)[5][1].split()
sephardic_words = []
for word in np.arange(0,len(sephardic))[::2]:
    sephardic_words.append(int(float(sephardic[word].split('*')[0])*1000)*[sephardic[word].split('*')[1].split('"')[1]])
# sephardic_words

In [ ]:
sources = ldamodel14.show_topics(num_topics=-1, num_words=50)[6][1].split()
sources_words = []
for word in np.arange(0,len(sources))[::2]:
    sources_words.append(int(float(sources[word].split('*')[0])*1000)*[sources[word].split('*')[1].split('"')[1]])
# sources_words


In [ ]:
philosophy = ldamodel14.show_topics(num_topics=-1, num_words=50)[7][1].split()
philosophy_words = []
for word in np.arange(0,len(philosophy))[::2]:
    philosophy_words.append(int(float(philosophy[word].split('*')[0])*1000)*[philosophy[word].split('*')[1].split('"')[1]])
# philosophy_words

In [ ]:
gender = ldamodel14.show_topics(num_topics=-1, num_words=50)[8][1].split()
gender_words = []
for word in np.arange(0,len(gender))[::2]:
    gender_words.append(int(float(gender[word].split('*')[0])*1000)*[gender[word].split('*')[1].split('"')[1]])
# gender_words

In [ ]:
america = ldamodel14.show_topics(num_topics=-1, num_words=50)[9][1].split()
america_words = []
for word in np.arange(0,len(america))[::2]:
    america_words.append(int(float(america[word].split('*')[0])*1000)*[america[word].split('*')[1].split('"')[1]])
# america_words


In [ ]:
yiddish = ldamodel14.show_topics(num_topics=-1, num_words=50)[10][1].split()
yiddish_words = []
for word in np.arange(0,len(yiddish))[::2]:
    yiddish_words.append(int(float(yiddish[word].split('*')[0])*1000)*[yiddish[word].split('*')[1].split('"')[1]])
# yiddish_words

In [ ]:
kabbalah = ldamodel14.show_topics(num_topics=-1, num_words=50)[11][1].split()
kabbalah_words = []
for word in np.arange(0,len(kabbalah))[::2]:
    kabbalah_words.append(int(float(kabbalah[word].split('*')[0])*1000)*[kabbalah[word].split('*')[1].split('"')[1]])
# kabbalah_words

In [ ]:
topics

In [ ]:
# Let's first check the first 50 and see what the min probability should be,
# and if the assigned topics make sense

art_topics_test = []
for article in np.arange(300,320):
    art_topics_test.append(ldamodel14.get_document_topics(corpus[article], 
                                           minimum_probability=0.15,   
                                                   # minprob will need to be adjusted based on no of topics generated by the model!
                                           minimum_phi_value=None, 
                                           per_word_topics=False)
#               .sort(key=itemgetter(1),reverse=True)
             )

In [ ]:
for i in art_topics_test:
    i.sort(key=itemgetter(1),reverse=True)
for k,v in enumerate(art_topics_test,start=300):
    print(k,v)

In [ ]:

#  # Load pickle
# with open('art_with_topics_book_ final.pickle','rb') as file:
#     art = pickle.load(file)

art_topics = []
for article in corpus:
    art_topics.append(ldamodel14.get_document_topics(article, 
                                           minimum_probability=0.15,   
                                                   # minprob will need to be adjusted based on no of topics generated by the model!
                                           minimum_phi_value=None, 
                                           per_word_topics=False)
#               .sort(key=itemgetter(1),reverse=True)
             )

In [ ]:
art_topics

In [ ]:
#filter articles for book reviews!
with open ('clean_data_full.pickle','rb') as file:
    art=pickle.load(file)

    

In [ ]:

print (len(art_topics))
print (len(art))


In [ ]:
# Ok, now let's add the topics to a list to add to the articles
art_topics = []
for article in corpus:
    art_topics.append(ldamodel14.get_document_topics(article, 
                                           minimum_probability=0.15,   
                                                   # minprob will need to be adjusted based on no of topics generated by the model!
                                           minimum_phi_value=None, 
                                           per_word_topics=False)
#               .sort(key=itemgetter(1),reverse=True)
             )

In [ ]:
# Let's see if the two line up
print(len(art_topics))
print(len(art))

In [ ]:
# Yep, so let's merge them
art['topics'] = art_topics

In [ ]:
# get max number of topics
art.topics.map(len).max()

In [ ]:

art[['topics']].head()


In [ ]:
for t in np.arange(0,12):
    art[topics[t]] = [[i[1] if i[0]==t else 0 for i in a] for a in art['topics']]
    art[topics[t]] = [[i for i in a if i > 0] for a in art[topics[t]]]
    art[topics[t]] = art[topics[t]].apply(lambda x: 0 if len(x)==0 else x[0])

In [ ]:
art.sort_values(by='topics',inplace=True)

In [ ]:
# remove duplicates
art.reset_index(inplace=True)
for i in np.arange(0,12):
    art.drop(i,inplace=True)
art.set_index('index',inplace=True)

In [ ]:
len(art)

In [ ]:
art.head()

In [ ]:
# Save to pickle
with open('art_with_topics_final_book.pickle','wb') as file:
    pickle.dump(art,file)

In [ ]:
with open('clean_data_full.pickle', 'rb') as file:
    raw = pickle.load(file)

In [ ]:
raw = raw[['year']].copy()

In [ ]:
raw.head()

In [ ]:
new=art.join(raw, on='index')

In [ ]:
len (new)

In [ ]:
new.head()

In [ ]:
# # load pickle
# with open('art_with_topics_final.pickle', 'rb') as file:
#     new = pickle.load(file)

In [ ]:
primary_counts = {}
for t in topics:
    primary_counts[topics[t]] = sum([1 if x[0][0] == t else 0 for x in new['topics']])

In [ ]:
primary_counts

In [ ]:
primary = pd.DataFrame(primary_counts,index=np.arange(0,15))
primary.rename(columns={0:'count'},inplace=True)
primary.to_csv('primary_topic_counts.csv',sep=',')


In [ ]:
secondary_counts = {}
for t in topics:
    secondary_counts[topics[t]] = {}
    for top in topics:
        secondary_counts[topics[t]][topics[top]] = sum(
            [1 if len(x)>1 and x[0][0] == t and x[1][0] == top else 0 for x in new['topics']])
secondary = pd.DataFrame(secondary_counts)
secondary

In [ ]:
secondary_counts = {}
for t in topics:
#     secondary_counts[topics[t]] = {}
    for top in topics:
        secondary_counts['{}_{}'.format(topics[t],topics[top])] = sum(
            [1 if len(x)>1 and x[0][0] == t and x[1][0] == top else 0 for x in new['topics']])
secondary_counts

In [ ]:
secondary = pd.DataFrame(secondary_counts,index=np.arange(0,15))
secondary = pd.DataFrame(secondary.iloc[0])
secondary.rename(columns={0:'count'},inplace=True)
secondary

In [ ]:
secondary.to_csv('secondary_topic_counts.csv',sep=',')


In [ ]:
new.head()

In [ ]:
years_strength = new.drop(['article_text','article_text_nostop_extra','string','topics'],axis=1).groupby('year').sum()

In [ ]:
years_strength

In [ ]:
years_count = new[['rabbinic','year']].groupby('year').count()
years_count.rename(columns={'rabbinic':'article_count'},inplace=True)
years_count

In [ ]:
years_strength = years_strength.join(years_count)
years_strength


In [ ]:
# Save to pickle
with open('topics_years_strength_book_final.pickle','wb') as file:
    pickle.dump(years_strength,file)

In [ ]:
years_strength.reset_index(inplace=True)
years_strength.head()

In [ ]:
years_strength.to_csv('tableau_years_strength_book_final.csv')